# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model
(Recurrent PPO) [default: 25 EVs per week simulation]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 563, done.
remote: Counting objects: 100% (170/170), done.
remote: Compressing objects: 100% (95/95), done.
remote: Total 563 (delta 91), reused 150 (delta 74), pack-reused 393
Receiving objects: 100% (563/563), 205.51 MiB | 25.80 MiB/s, done.
Resolving deltas: 100% (240/240), done.
Checking out files: 100% (225/225), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          RL_VPP_Thesis/
Algorithm_simulator_notebooks/    trained_models/
data/                             VPP_environment.py
EV_experiment_notebooks/          VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  wandb/
README.md


In [3]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.15
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.15', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.15\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f615e5de350>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 25
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 25, 'EVs_n_max': 1305, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_Dataset_autarky()

Charging event: 1, Arrival time: 2022-01-01 10:15:00, Parking_time: 24, Leaving_time: 2022-01-02 10:15:00, SOC: 0.645445001242038, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 1304, Arrival time: 2022-12-31 11:45:00, Parking_time: 22.836166342022242, Leaving_time: 2023-01-01 10:35:10.198831, SOC: 0.4522809373980031, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -21214.64 , Grid_used_en(grid-import)=4947.18kWh , autarky-rate=83.0 , RE-to-vehicle_unused_en(grid-export)=-26161.81kWh , self-consump.rate=47.9 , Total_selling_cost=€  -489.75 , Grid_cost=€  233.11
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  27146.95 , Grid_used_en=kWh  43110.76 , RE-to-vehicle_unused_en=kWh  15963.81 , Total_selling_cost=€  1085.99 , Grid_cost=€  1548.42 , Charging_events=  1304 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  70.06


In [7]:
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [8]:
env.plot_ELVIS_data()

In [9]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  27066.24 , Grid_used_en(grid-import)=42862.0kWh , Total_demand=77342.13kWh , autarky-rate=0.4 , RE-to-vehicle_unused_en(grid-export)=15795.76kWh , Total_supply=50275.89kWh , self-consump.rate=0.7 , Grid_cost=€  1500.43 , Total_selling_cost=€  1052.39 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [10]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
#env.plot_Elvis_results()

In [12]:
#env.plot_VPP_results()

In [13]:
env.plot_VPP_autarky()

In [14]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
env.plot_VPP_Elvis_comparison()

In [16]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [17]:
#env.plot_rewards_stats()

In [18]:
env.plot_EVs_kpi()

In [19]:
env.plot_actions_kpi()

In [20]:
env.plot_load_kpi()

In [21]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [22]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [23]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [24]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  27660.71 , Grid_used_en(grid-import)=44070.8kWh , Total_demand=77929.5kWh , autarky-rate=0.4 , RE-to-vehicle_unused_en(grid-export)=16410.08kWh , Total_supply=50268.78kWh , self-consump.rate=0.7 , Grid_cost=€  1539.67 , Total_selling_cost=€  1056.97 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -2665.45 , Grid_used_en(grid-import)=1507.84kWh , Total_demand=79932.35kWh , autarky-rate=42.4 , RE-to-vehicle_unused_en(grid-export)=4173.3kWh , Total_supply=37136.08kWh , self-consump.rate=91.3 , Total_selling_cost=€  -62.72 , Grid_cost=€  53.43 
 EV_INFO: Av.EV_energy_leaving=kWh  64.27 , Std.EV_energy_leaving=kWh  24.39 , EV_departures =  1303 , EV_queue_left =  1
SCORE:  Cumulative_reward= 450526.76 - Step_rewars (load_t= 410566.95, EVs_energ

In [25]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [26]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  54.065269  36.358067  43.717800  47.164822   
2022-01-01 00:15:00  54.315269  35.729824  43.089558  47.414822   
2022-01-01 00:30:00  54.565269  35.152897  42.512630  47.664822   
2022-01-01 00:45:00  54.815269  34.583714  41.943447  47.914822   
2022-01-01 01:00:00  55.065269  34.035236  41.394970  48.164822   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  57.793373  71.212296  66.640869   0.000000   
2022-06-06 05:00:00  59.232948  71.212296  68.080444   0.000000   
2022-06-06 05:15:00  60.881256  71.212296  69.728752   0.000000   
2022-06-06 05:30:00  62.416798  71.212296  71.264297   0.000000   
2022-06-06 05:45:00  63.878086  71.212296  72.725586   0.000000   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [3910, 3908, 3911, 3909]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [3910, 3908, 3911, 3909]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [3910, 3908, 3911, 3909]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [3910, 3908, 3911, 3909]  [1, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00     [4479, 4478, 4480, 0]  [1, 0, 1, 2]   
2022-06-06 05:00:00     [4479, 4478, 4480, 0]  [1, 0, 1, 2]   
2022-06-06 05:15:00     [4479, 4478, 4480, 0]  [1, 0, 1, 2]   
2022-06-06 05:30:00     [4479, 4478, 4480, 0]  [1, 0, 1, 2]   
2022-06-06 05:45:00     [4479, 4478, 4480, 0]  [1, 0, 1, 2]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00    [False, True, True, False]        2.000000   
2022-01-01 00:30:00    [False, True, True, False]        2.000000   
2022-01-01 00:45:00    [False, True, True, False]        2.000000   
2022-01-01 01:00:00    [False, True, True, False]        2.000000   
...                                           ...             ...   
2022-06-06 04:45:00     [True, True, True, False]        8.517743   
2022-06-06 05:00:00     [True, True, True, False]       11.516608   
2022-06-06 05:15:00     [True, True, True, False]       13.186449   
2022-06-06 05:30:00     [True, True, True, False]       12.284334   
2022-06-06 05:45:00     [True, True, True, False]       11.690294   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  2.267347e+00         15.0        0.0   
2022-01-01 00:15:00          -5.025933  0.000000e+00         15.0        0.0   
2022-01-01 00:30:00          -4.615409 -4.440892e-16         15.0        0.0   
2022-01-01 00:45:00          -4.553456  0.000000e+00         15.0        0.0   
2022-01-01 01:00:00          -4.387806  0.000000e+00         15.0        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00           0.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:00:00           0.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:15:00           0.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:30:00           0.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:45:00           0.000000  0.000000e+00         15.0        0.0   

                     rewards  
time                          
2022-01-01 00:00:00     15.0  
2022-01-01 00:15:00     15.0  
2022-01-01 00:30:00     15.0  
2022-01-01 00:45:00     15.0  
2022-01-01 01:00:00     15.0  
...                      ...  
2022-06-06 04:45:00     15.0  
2022-06-06 05:00:00     15.0  
2022-06-06 05:15:00     15.0  
2022-06-06 05:30:00     15.0  
2022-06-06 05:45:00     15

In [27]:
#env.plot_Elvis_results()

In [28]:
#env.plot_VPP_results()

In [29]:
env.plot_VPP_autarky()

In [30]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [31]:
env.plot_VPP_Elvis_comparison()

In [32]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [33]:
env.plot_rewards_stats()

In [34]:
env.plot_EVs_kpi()

In [35]:
env.plot_load_kpi()

In [36]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [37]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 5217, Arrival time: 2022-01-01 07:00:00, Parking_time: 24, Leaving_time: 2022-01-02 07:00:00, SOC: 0.47863603916671826, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 6520, Arrival time: 2022-12-31 22:45:00, Parking_time: 24, Leaving_time: 2023-01-01 22:45:00, SOC: 0.7771486793964677, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , Grid_used_en(grid-import)=2136.67kWh , autarky-rate=89.6 , RE-to-vehicle_unused_en(grid-export)=-32222.06kWh , self-consump.rate=36.4 , Total_selling_cost=€  -1187.15 , Grid_cost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  16755.6 , Grid_used_en=kWh  37672.1 , RE-to-vehicle_unused_en=kWh  20916.5 , Total_selling_cost=€  797.98 , Grid_cost=€  1651.38 , Charging_events=  1304 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  74.71


In [38]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [39]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [40]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18908.46 , Grid_used_en(grid-import)=39364.31kWh , Total_demand=69539.34kWh , autarky-rate=0.4 , RE-to-vehicle_unused_en(grid-export)=20455.84kWh , Total_supply=50630.88kWh , self-consump.rate=0.6 , Grid_cost=€  1722.25 , Total_selling_cost=€  896.69 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  74.71
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4435.26 , Grid_used_en(grid-import)=994.75kWh , Total_demand=73264.56kWh , autarky-rate=37.2 , RE-to-vehicle_unused_en(grid-export)=5430.01kWh , Total_supply=31683.95kWh , self-consump.rate=86.1 , Total_selling_cost=€  -160.29 , Grid_cost=€  42.4 
 EV_INFO: Av.EV_energy_leaving=kWh  69.83 , Std.EV_energy_leaving=kWh  23.45 , EV_departures =  1299 , EV_queue_left =  1
SCORE:  Cumulative_reward= 465977.78 - Step_rewars (load_t= 397927.47, EVs_ener

In [41]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
VPP_table.head(15000)

0          1          2          3  \
time                                                        
2022-01-01 00:00:00  0.0   0.000000   0.000000   0.000000   
2022-01-01 00:15:00  0.0   0.000000   0.000000   0.000000   
2022-01-01 00:30:00  0.0   0.000000   0.000000   0.000000   
2022-01-01 00:45:00  0.0   0.000000   0.000000   0.000000   
2022-01-01 01:00:00  0.0   0.000000   0.000000   0.000000   
...                  ...        ...        ...        ...   
2022-06-06 04:45:00  0.0  83.117363  82.385590  77.976921   
2022-06-06 05:00:00  0.0  84.252983  83.521210  79.112541   
2022-06-06 05:15:00  0.0  85.510391  84.778618  80.369949   
2022-06-06 05:30:00  0.0  86.737320  86.005547  81.596878   
2022-06-06 05:45:00  0.0  87.950500  87.218727  82.810059   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00           [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00           [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00           [0, 0, 0, 0]  [2, 0, 1, 0]   
2022-01-01 01:00:00           [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                    ...           ...   
2022-06-06 04:45:00  [0, 8365, 8367, 8366]  [2, 1, 1, 1]   
2022-06-06 05:00:00  [0, 8365, 8367, 8366]  [2, 1, 1, 1]   
2022-06-06 05:15:00  [0, 8365, 8367, 8366]  [2, 1, 1, 1]   
2022-06-06 05:30:00  [0, 8365, 8367, 8366]  [2, 1, 1, 1]   
2022-06-06 05:45:00  [0, 8365, 8367, 8366]  [2, 1, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00   [False, True, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00    [False, True, True, True]       10.255554   
2022-06-06 05:00:00    [False, True, True, True]       13.627466   
2022-06-06 05:15:00    [False, True, True, True]       15.088909   
2022-06-06 05:30:00    [False, True, True, True]       14.723161   
2022-06-06 05:45:00    [False, True, True, True]       14.558124   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0 -3.182998e+00    -3.856393        0.0   
2022-01-01 00:15:00                0.0 -3.313836e+00    -5.262133        0.0   
2022-01-01 00:30:00                0.0 -4.288346e+00    -5.324394        0.0   
2022-01-01 00:45:00                0.0 -4.356833e+00    -4.717548        0.0   
2022-01-01 01:00:00                0.0 -3.830529e+00    -4.301072        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00                0.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:00:00                0.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:15:00                0.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:30:00                0.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:45:00                0.0  1.776357e-15    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -3.856393  
2022-01-01 00:15:00  -5.262133  
2022-01-01 00:30:00  -5.324394  
2022-01-01 00:45:00  -4.717548  
2022-01-01 01:00:00  -4.301072  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:45:00  15.000000  

[15000 rows x 13 columns]

In [43]:
#env.plot_VPP_results()


In [44]:
env.plot_VPP_autarky()

In [ ]:
env.plot_VPP_supply_demand()

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

In [ ]:
env.plot_VPP_energies()

In [ ]:
VPP_table.head(14995)

In [ ]:
#env.plot_VPP_results()

In [ ]:
env.plot_VPP_autarky()

In [ ]:
env.plot_VPP_supply_demand()

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

In [ ]:
#env.close()